### Data Set: Tokyo
Visualización de datos del data set Tokyo.</br>
Exportación de librerias de Visualización del data set:

In [24]:
#Pandas gui: App basada den plotly
from pandasgui import show

#Librerías básicas de data
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

#Librerias visualización de gráficas
import plotly.express as px
import plotly.graph_objects as go

#Librería para mapa 
from geopy.distance import great_circle


## ¿Cómo afrontar el análisis?

Al no tener preguntas que resolver por parte del cliente, se realzará un análisis de datos generalista con los datos proporcionados.
En este caso, intentaremos despejar las claves principales a la hora de reservar y/o decicir que tipo de alomajamiento alquilamos: 
las pernoctas, la situación geográfica y si influye de alguna forma las reseñas que tiene cada alojamiento.





# Visualización de datos


#### Tenemos las siguientes columnas:

- **id:** Un identificador único para cada registro en tu conjunto de datos. 
- **name:** El nombre del alojamiento.
- **host_id:** El identificador único del anfitrión.
- **host_name:** El nombre del anfitrión.
- **neighbourhood_group:** La agrupación o categorización de vecindarios más grande o de nivel superior en una ciudad o área geográfica.
- **neighbourhood:** El nombre del vecindario o área geográfica específica en la que se encuentra la propiedad. Esto proporciona información sobre la ubicación de la propiedad. En este data set hay 4 tipos: **- ku: Distrito, - shi: Gran Ciudad, - machi: Ciudad, - mura: Pueblo.**
- **latitude:** La latitud geográfica de la ubicación de la propiedad. 
- **longitude:** La longitud geográfica de la ubicación de la propiedad. 
- **room_type:** El tipo de habitación o alojamiento, en este dataset: "habitación privada", "casa/apartamento completo" o "habitación compartida".
- **price:** El precio de alquiler por noche o por estancia en la propiedad. 
- **minimum_nights:** El número mínimo de noches que un huésped debe reservar para quedarse en la propiedad.
- **number_of_reviews:** El número total de revisiones o comentarios que ha recibido la propiedad hasta la fecha.
- **last_review:** La fecha de la última revisión o comentario dejado por un huésped en la propiedad.
- **reviews_per_month:** El promedio de revisiones o comentarios dejados por los huéspedes por mes.



In [25]:
df = pd.read_csv("../data/tokyo_airbnb.csv")
df.head()

id  ... reviews_per_month
0   35303  ...              0.20
1  197677  ...              1.65
2  289597  ...              1.25
3  370759  ...              1.55
4  700253  ...              1.24

[5 rows x 14 columns]

In [26]:
show (df)

PandasGUI INFO — pandasgui.gui — Opening PandasGUI
C:\Users\psych\AppData\Local\Temp\ipykernel_21296\603652372.py:1: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

C:\Users\psych\AppData\Local\Temp\ipykernel_21296\603652372.py:1: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

C:\Users\psych\AppData\Local\Temp\ipykernel_21296\603652372.py:1: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

C:\Users\psych\AppData\Local\Temp\ipykernel_21296

Después de ver todas las columnas que tiene el data set, miramos datos más específicos: 
El dataSet se compone de 14 columnas y 11466 fila. 
También hemos calculado:

- Valores únicos
- Ausencia de valores 
- Porcentaje de ausencia de valores
- Duplicado
- Tipo de valores

In [27]:
def summary(df):
    total_values = df.shape[0]
    missing_data = df.isnull().sum()
    missing_percentage = (missing_data / total_values) * 100
    duplicated_counts = [df[col].duplicated().sum() for col in df.columns]
    print(f"Dataset has {df.shape[1]} features and {df.shape[0]} rows.")

    summary = pd.DataFrame(index=df.columns)
    summary["Unique"] = df.nunique().values
    summary["Missing"] = df.isnull().sum().values
    summary['Missing %'] = ((missing_data / total_values) * 100).round(2)    
    summary["Duplicated"] = duplicated_counts
    summary["Types"] = df.dtypes
    
    return summary

summary(df)

Dataset has 14 features and 11466 rows.


Unique  Missing  Missing %  Duplicated    Types
id                    11466        0       0.00           0    int64
name                  10810        0       0.00         656   object
host_id                2954        0       0.00        8512    int64
host_name              2054       16       0.14        9411   object
neighbourhood_group       0    11466     100.00       11465  float64
neighbourhood            56        0       0.00       11410   object
latitude               7295        0       0.00        4171  float64
longitude              8140        0       0.00        3326  float64
room_type                 3        0       0.00       11463   object
price                   371        0       0.00       11095    int64
minimum_nights           30        0       0.00       11436    int64
number_of_reviews       251        0       0.00       11215    int64
last_review             413     1677      14.63       11052   object
reviews_per_month       692     1677      14.63       10773  float64

In [28]:
df.drop('neighbourhood_group', axis=1, inplace=True)

La columna que no tiene ninguna importancia dentro de la ciudad de Tokyo es: neighbourhood_group, ya que el peso de porcentajes ausentes es del 100%. 
Las columnas last_review, reviews_per_month tiene un porcentaje de usencia del 14,63%. Esto va a ser un problema más adelante, pero las necesitaremos para ver si se cumplen un par de hipótesis planteandas sobre el comportamiento de los usuarios a la hora de alquilar sin importar las noches, el precio por noche y/o el tipo de habitación.


Viéndo por encima el data set, nos surgen las primeras hipótesis en las que estaremos trabajando, hasta que los datos nos muestren lo contrario: 

## Hipótesis: 

- Influencia de geografica y zonas de interés
- Tipo de habitación por precio
- Tipo de habitación por precio, zona y noches mínimas
- Afectación de las rewievs con el alquiler.



Antes de ponernos con las hipótesis, crearemos una columna nueva que discrimina por tipo de zonas dentro de Tokyo. Observando el dataset, se puede ver como todas las ciudades tiene una terminación en común, son designaciones de las zonas las que se encuentran, siendo esto bastante importante para nuestra primera hipótesis

In [29]:
df[['neighbourhood', 'Type']] = df['neighbourhood'].str.split(' ', expand=True)

df.head(1)


id  ... Type
0  35303  ...   Ku

[1 rows x 14 columns]

# Primera Hipótesis: 
Precio por tipo de zona, y cercanía a puntos de interés.
A mayor cercanía al puntos de interés, más elevado será el precio de alquiler.

En el dataset proporcionado no hay puntos de interés, asi que pondremos los 20 sitios más populares de Tokyo dentro de una variable:

- **Tokyo Tower**: Situada en Minato, ofrece vistas panorámicas de la ciudad.
- **Tokyo Skytree**:  La torre de radiodifusión más alta del mundo.
- **Templo Sensō-ji**: El templo budista más antiguo de Tokio.
- **Shibuya Crossing**: El cruce de peatones más concurrido del mundo.
- **Ginza**: El distrito de compras más famoso de Tokio.
- **Harajuku**: Conocido por su moda extravagante y tiendas únicas.
- **Meiji Shrine**: Un importante santuario sintoísta rodeado de bosques.
- **Akihabara**: El paraíso de la tecnología y cultura pop.
- **Ueno Park**: Un parque enorme con museos y el zoológico de Ueno.
- **Asakusa**: Hogar del Templo Sensō-ji y calles llenas de historia.
- **Odaiba**: Una isla artificial con centros comerciales y atracciones.
- **Roppongi Hills**: Un complejo urbano con tiendas, restaurantes y arte.
- **Imperial Palace** Residencia oficial del Emperador de Japón.
- **Tokyo Disneyland**: Uno de los parques de Disney más grandes del mundo.
- **Tsukiji Fish Market**: El mercado de pescado más grande y famoso de Tokio.
- **Sumida Aquarium**: Un acuario único en la base de la Tokyo Skytree.
- **National Museum of Emerging Science and Innovation**: Un museo interactivo de ciencia y tecnología.
- **Tokyo Midtown**: Un complejo comercial y de entretenimiento en Roppongi.
- **Shinjuku Gyoen National Garden**: Un hermoso jardín botánico en el corazón de la ciudad.
- **Oedo Onsen Monogatari**: Un parque temático de aguas termales al estilo onsen en Odaiba.


In [42]:
# Lista de sitios turísticos en Tokio con sus coordenadas (latitud, longitud)
turistic_place = [
{"name": "Tokyo Tower", "latitude": 35.6586, "longitude": 139.7454},
{"name": "Tokyo Skytree", "latitude": 35.7101, "longitude": 139.8107},
{"name": "Templo Sensō-ji", "latitude": 35.7149, "longitude": 139.7967},
{"name": "Shibuya Crossing", "latitude": 35.6604, "longitude": 139.6982},
{"name": "Ginza", "latitude": 35.6712, "longitude": 139.7649},
{"name": "Harajuku", "latitude": 35.6714, "longitude": 139.7035},
{"name": "Meiji Shrine", "latitude": 35.6764, "longitude": 139.6993},
{"name": "Akihabara", "latitude": 35.6995, "longitude": 139.7710},
{"name": "Ueno Park", "latitude": 35.7146, "longitude": 139.7736},
{"name": "Asakusa", "latitude": 35.7140, "longitude": 139.7967},
{"name": "Odaiba", "latitude": 35.6190, "longitude": 139.7798},
{"name": "Roppongi Hills", "latitude": 35.6604, "longitude": 139.7295},
{"name": "Imperial Palace", "latitude": 35.6828, "longitude": 139.7595},
{"name": "Tokyo Disneyland", "latitude": 35.6329, "longitude": 139.8808},
{"name": "Tsukiji Fish Market", "latitude": 35.6653, "longitude": 139.7707},
{"name": "Sumida Aquarium", "latitude": 35.7100, "longitude": 139.8107},
{"name": "National Museum of Emerging Science and Innovation", "latitude": 35.6197, "longitude": 139.7797},
{"name": "Tokyo Midtown", "latitude": 35.6653, "longitude": 139.7300},
{"name": "Shinjuku Gyoen National Garden", "latitude": 35.6852, "longitude": 139.7108},
{"name": "Oedo Onsen Monogatari", "latitude": 35.6343, "longitude": 139.7773},
]

In [43]:
# Calcular la distancia entre cada propiedad y los sitios turísticos en Tokio
for sitio in turistic_place:
    sitio_lat = sitio["latitude"]
    sitio_lon = sitio["longitude"]
    sitio_name = sitio["name"]
    
    # Calcular la distancia y agregarla como una nueva columna al df
    df[sitio_name + "_distance"] = df.apply(lambda row: great_circle((row["latitude"], row["longitude"]), (sitio_lat, sitio_lon)).kilometers, axis=1)

# crear mapa con marcadores
fig = go.Figure()

# Añadir marcadores de sitios turísticos
for sitio in turistic_place:
    fig.add_trace(go.Scattermapbox(
        lat=[sitio["latitude"]],
        lon=[sitio["longitude"]],
        mode='markers',
        marker=go.scattermapbox.Marker(size=10, color='red'),
        text=sitio["name"],
        name=sitio["name"]
    ))

# Crear un mapa de calor para los precios de alquiler
fig.add_trace(px.density_mapbox(df, 
                                 lat="latitude", 
                                 lon="longitude", 
                                 z="price", 
                                 radius=13,
                                 color_continuous_scale="Viridis",
                                 opacity=0.5).data[0])

# Configurar diseño del mapa
fig.update_layout(
    legend=dict(x=0, y=1, traceorder='grouped', orientation='h'),
    mapbox_style="carto-positron",
    mapbox_zoom=10,
    mapbox_center={"lat": df["latitude"].mean(), "lon": df["longitude"].mean()}
)

# Mostrar el mapa.
fig.show()

#### Segunda hipótesis:
Precio según tipo de zona. 
En tokyo hay gran tipos de zonas, en el data set tenemos cuatro siendo: **- ku: Distrito, - shi: Gran Ciudad, - machi: Ciudad, - mura: Pueblo.**
Puede que haya una fuerte relación entre la zona en la que se encuentra el alojamiento con el precio que este tiene. 
Primero calcularemos el precio medio de alquiler, y el impacto respespecto a las otras zonas. 
Se observa que Ku y Shi tiene un gran impacto de alquiler y son las más elevadas a la hora de alquilar.

In [45]:
# Calcular la media de la columna 'price' por 'Type' y redondear a dos decimales
media_precios_por_barrio = df.groupby('Type')['price'].mean().round(2)

# Calcular porcentajes de influencia entre los valores medios
influencia_porcentual = (media_precios_por_barrio / media_precios_por_barrio.sum()) * 100

# Redondear los porcentajes de influencia a dos números después de la coma
influencia_porcentual = influencia_porcentual.round(2)

# Crear un DataFrame con los resultados
resultados = pd.DataFrame({
    'Barrio': media_precios_por_barrio.index,
    'Precio Medio': media_precios_por_barrio.values,
    'Porcentaje de Influencia': influencia_porcentual.values
})

resultados

Barrio  Precio Medio  Porcentaje de Influencia
0     Ku      13042.52                     30.00
1  Machi      10232.16                     23.54
2   Mura      11820.86                     27.19
3    Shi       8377.69                     19.27

Mapeamos para ver como de influyentes son los alquileres respecto al centro de una forma mucho más visual. 

In [46]:
# Crear un mapa interactivo delimitando por Type
fig = px.scatter_mapbox(df, 
                        lat="latitude", 
                        lon="longitude", 
                        color="Type",
                        hover_name="Type",
                        category_orders={"Type": ["Ku", "Shi", "Mura", "Machi"]},
                        labels={"Type": "Tipos de Zona"},
                        zoom=10,
                        mapbox_style="carto-positron")

# Configurar diseño del mapa
fig.update_layout(
    title_text='Mapa por tipo de zonas',
    mapbox_layers=[
        {
            "below": 'traces',
            "sourcetype": "raster",
            "source": [
                "https://basemap.nationalmap.gov/arcgis/rest/services/USGSImageryOnly/MapServer/tile/{z}/{y}/{x}"
            ]
        }
      ])

# Mostrar el mapa interactivo
fig.show()


Observamos unos precios fuera de rango, que más tarde investigaremos. 

La demanda y el precio medio en Ku, y Shi, hacen que sea las zonas más alquiladas debido a su cercanía con varios puntos de interés y ser las zonas más "urbanitas" 

In [47]:
# Crear gráficas separadas para cada tipo de habitación
fig = px.box(df, x="Type", y="price", 
             category_orders={"Type": ["Ku", "Shi", "Mura", "Machi"]},
             labels={"Type": "Tipo de Zona", "price": "Precio de Alquiler"},
             title="Influencia del tipo de zona en el Precio de Alquiler",
             hover_data=["name", "room_type"],
             facet_col="room_type")  # Utiliza el argumento facet_col para separar por tipo de habitación

# Mostrar las gráficas interactivas
fig.show()


#### Tercera hipótesis:
Influencia de las interaciones de otros usuarios mediante las reseñas a la hora de alquilar y precio.
Lo primero de todo es hacer un análisis de correlación

In [48]:
# Calcular la matriz de correlación
correlacion = df[['number_of_reviews', 'reviews_per_month', 'price']].corr().round(2)

# Mostrar la matriz de correlación
correlacion


number_of_reviews  reviews_per_month  price
number_of_reviews               1.00               0.48  -0.01
reviews_per_month               0.48               1.00   0.10
price                          -0.01               0.10   1.00

In [49]:
# Calcular el número total de alquileres para cada propiedad
total_alquileres = df['number_of_reviews'].sum()

# Mostrar el número total de alquileres
print(f"Número total de alquileres: {total_alquileres}")


Número total de alquileres: 298447


In [50]:

# Scatter plot para number_of_reviews vs price
fig1 = px.scatter(df, x='number_of_reviews', y='price', title='Número de Revisiones vs Precio')

# Scatter plot para reviews_per_month vs price
fig2 = px.scatter(df, x='reviews_per_month', y='price', title='Revisiones por Mes vs Precio')

# Mostrar los scatter plots
fig1.show()
fig2.show()

#### Cuarta Hipótesis:
Influencia en el número de noches



In [51]:
# Crear un gráfico interactivo de dispersión para 'minimum_nights' vs 'price' y 'host_name'
fig = px.scatter(df, x='minimum_nights', y='price', color='Type',
                 labels={'minimum_nights': 'Número Mínimo de Noches', 'price': 'Precio', 'host_name': 'Nombre del Anfitrión'},
                 title='Relación entre Número Mínimo de Noches, Precio y Nombre del Anfitrión')

# Mostrar el gráfico interactivo
fig.show()

#### Outliers

In [52]:
def outliers(df, columna):
    # Calcula el primer cuartil (Q1)
    q1 = df[columna].quantile(0.25)

    # Calcula el tercer cuartil (Q3)
    q3 = df[columna].quantile(0.75)

    # Calcula el IQR
    iqr = q3 - q1

    # Imprime los valores de Q1, Q3 y el IQR
    print("Q1:", q1)
    print("Q3:", q3)
    print("IQR:", iqr)

    # Calcula los límites inferior y superior del rango válido
    inferior = q1 - 1.5 * iqr
    superior = q3 + 1.5 * iqr

    # Sustituye los valores fuera del rango con los límites
    df[columna] = df[columna].apply(lambda x: inferior if x < inferior else (superior if x > superior else x))
    
    return df

df = outliers(df, 'price')

Q1: 6026.0
Q3: 17216.0
IQR: 11190.0
